In [1]:
import pandas as pd
import numpy as np
import sklearn
from sklearn.metrics import mean_squared_error,r2_score
import sklearn.metrics
import warnings
import xgboost as xgb
import scipy as sc
import math
import matplotlib.pyplot as plt
import seaborn as sns
plt.style.use('ggplot')
import lightgbm as lgb
from sklearn.preprocessing import StandardScaler
import warnings
warnings.filterwarnings('ignore')
from sklearn import metrics
from sklearn.linear_model import LogisticRegression
from sklearn import svm
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import KFold
from math import sqrt
from sklearn import svm, datasets
from sklearn.metrics import r2_score
from sklearn.metrics import roc_curve, auc
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import Ridge
from xgboost import XGBRegressor
from sklearn.svm import SVR
from sklearn.ensemble import VotingClassifier
from sklearn.model_selection import cross_val_score
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn import datasets
from lightgbm import LGBMClassifier
from sklearn.ensemble import StackingClassifier
from sklearn.model_selection import StratifiedKFold
from bayes_opt import BayesianOptimization
import os
from matplotlib.font_manager import FontProperties

In [3]:
!pip list 

Package                      Version
---------------------------- -----------
absl-py                      1.4.0
anyio                        3.5.0
argon2-cffi                  21.3.0
argon2-cffi-bindings         21.2.0
asttokens                    2.0.5
astunparse                   1.6.3
attrs                        22.1.0
backcall                     0.2.0
bayesian-optimization        1.4.2
BayesianOptimization         0.0.0
beautifulsoup4               4.11.1
bleach                       4.1.0
Boruta                       0.3
cachetools                   5.3.0
catboost                     1.2
category-encoders            1.1.2
certifi                      2022.12.7
cffi                         1.15.1
charset-normalizer           3.1.0
cloudpickle                  2.2.1
cmapPy                       4.0.1
colorama                     0.4.6
comm                         0.1.2
contourpy                    1.0.7
cycler                       0.11.0
debugpy                      1.5.1
decora

# Define function

In [4]:
def get_data(cv):
    Train_metadata= pd.read_csv('Y_train20230610.csv')
    Test_metadata= pd.read_csv('Y_test20230610.csv')    
    Train_signature= pd.read_csv('X_train_RRA_CV80_20230630.csv',index_col=0)
    Test_signature= pd.read_csv('X_test_RRA_CV80_20230630.csv',index_col=0)    
    Y_train_val=Train_metadata[cv]
    Y_test=Test_metadata[cv]    
    X_train_val=Train_signature
    X_test=Test_signature                   
    X_all=pd.concat([Train_signature,Test_signature], axis=0)
    Y_all=pd.concat([Y_train_val,Y_test], axis=0)
    return X_train_val,Y_train_val,X_test,Y_test,X_all,Y_all

In [5]:
def get_stacking():
 # define the base models
    level0 = list()
    #level0.append(('lr', LogisticRegression()))
    level0.append(('svm', model1))
    level0.append(('RF', model2))
    level0.append(('XGB',model3))
    level0.append(('LGB', model4))
 # define meta learner model
    level1 = LogisticRegression()
 # define the stacking ensemble
    model = StackingClassifier(estimators=level0, final_estimator=level1)
    return model

In [ ]:

model1=SVC(probability=True,kernel='rbf')
model2=RandomForestClassifier(random_state=123,class_weight='balanced')
model3=xgb.XGBClassifier(random_state=123,is_unbalance=True)
model4=LGBMClassifier(random_state=123,class_weight='balanced')
model5=VotingClassifier(estimators=[('SVC',model2),('RF',model2),('XGB',model3),('LGB',model4)],voting='soft')
model6=get_stacking()

In [6]:
def model_score(name,X_train_val,Y_train_val,X_test,Y_test,model1,model2,model3,model4,model5,model6):
    df = pd.DataFrame()
    for model,label in zip([model1,model2,model3,model4,model5,model6],['SVM','RF','XGB','LGB','Voting','Stacking']):    
        model.fit(X_train_val, Y_train_val)
        predict_test = model.predict(X_test)
        prob_test = model.predict_proba(X_test)
        predict_test_value = prob_test[:, 1]
        report=sklearn.metrics.classification_report(Y_test, predict_test,output_dict=True)        
        df_1= pd.DataFrame(report).transpose()        
        df=pd.concat([df,df_1],axis=0) 
        print(label,"ROC_AUC:",sklearn.metrics.roc_auc_score(Y_test,predict_test_value),sklearn.metrics.classification_report(Y_test, predict_test))    
    from sklearn.metrics import roc_curve as ROC  
    from sklearn.metrics import auc as AUC   
    plt.figure(dpi=6000,figsize=(4,3))
    sns.set_palette('GnBu',5)
    sns.set(style='whitegrid')
    plt.xlabel('FPR',size=12, weight='bold')
    plt.ylabel('TPR',size=12, weight='bold')
    y_true=Y_test
    model1.fit(X_train_val, Y_train_val)   
    predict_test = model1.predict(X_test)
    prob_test = model1.predict_proba(X_test)
    predict_test_value = prob_test[:, 1]
    fpr1, tpr1, thresholds = metrics.roc_curve( Y_test,predict_test_value)
    roc_auc1 = metrics.auc(fpr1, tpr1)
    auc1=str(AUC(fpr1,tpr1))[:4]
    plt.plot(fpr1, tpr1, lw=1.5)
    x1=pd.concat([pd.DataFrame(fpr1),pd.DataFrame(tpr1)],axis=1)
    
    model2.fit(X_train_val, Y_train_val)
    predict_test = model2.predict(X_test)
    prob_test = model2.predict_proba(X_test)
    predict_test_value = prob_test[:, 1]
    fpr2, tpr2, thresholds = metrics.roc_curve(Y_test,predict_test_value)
    roc_auc2 = metrics.auc(fpr2, tpr2)
    auc2=str(AUC(fpr2,tpr2))[:4]
    plt.plot(fpr2, tpr2, lw=1.5)
    x2=pd.concat([pd.DataFrame(fpr2),pd.DataFrame(tpr2)],axis=1)
    model3.fit(X_train_val, Y_train_val)
    predict_test = model3.predict(X_test)
    prob_test = model3.predict_proba(X_test)
    predict_test_value = prob_test[:, 1]
    fpr3, tpr3, thresholds = metrics.roc_curve( Y_test,predict_test_value)
    roc_auc3 = metrics.auc(fpr3, tpr3)
    auc3=str(AUC(fpr3,tpr3))[:4]
    plt.plot(fpr3, tpr3, lw=1.5)
    x3=pd.concat([pd.DataFrame(fpr3),pd.DataFrame(tpr3)],axis=1)
    model4.fit(X_train_val, Y_train_val)
    predict_test = model4.predict(X_test)
    prob_test = model4.predict_proba(X_test)
    predict_test_value = prob_test[:, 1]
    fpr4, tpr4, thresholds = metrics.roc_curve( Y_test,predict_test_value)
    roc_auc4 = metrics.auc(fpr4, tpr4)
    print("model4:",roc_auc4)
    auc4=str(AUC(fpr4,tpr4))[:4]
    plt.plot(fpr4, tpr4, lw=1.5)
    x4=pd.concat([pd.DataFrame(fpr4),pd.DataFrame(tpr4)],axis=1)
    model5.fit(X_train_val, Y_train_val)
    predict_test = model5.predict(X_test)
    prob_test = model5.predict_proba(X_test)
    predict_test_value = prob_test[:, 1]
    fpr5, tpr5, thresholds = metrics.roc_curve( Y_test,predict_test_value)
    roc_auc5 = metrics.auc(fpr5, tpr5)
    print("model5:",roc_auc5)
    auc5=str(AUC(fpr5,tpr5))[:4]
    plt.plot(fpr5, tpr5, lw=1.5)
    x5=pd.concat([pd.DataFrame(fpr5),pd.DataFrame(tpr5)],axis=1)
    model6.fit(X_train_val, Y_train_val)
    predict_test = model6.predict(X_test)
    prob_test = model6.predict_proba(X_test)
    predict_test_value = prob_test[:, 1]
    fpr6, tpr6, thresholds = metrics.roc_curve( Y_test,predict_test_value)
    roc_auc6 = metrics.auc(fpr6, tpr6)
    print("model6:",roc_auc6)
    auc6=str(AUC(fpr6,tpr6))[:4]
    plt.plot(fpr6, tpr6, lw=1.5)
    x6=pd.concat([pd.DataFrame(fpr6),pd.DataFrame(tpr6)],axis=1)
    plt.legend(['SVM: AUC = %0.4f' % roc_auc1,
            'RF: AUC = %0.4f' % roc_auc2,
            'XGB: AUC = %0.4f' % roc_auc3,
            'LGB: AUC = %0.4f' % roc_auc4,
            'Voting: AUC = %0.4f' % roc_auc5,
            'Stacking: AUC = %0.4f' % roc_auc6

                ],loc=0, prop=FontProperties(weight='bold',size=10))
    plt.ylim(0,1.1)
    plt.xticks(size=12, weight='bold')
    plt.yticks(size=12, weight='bold')
    plt.tight_layout() 
    plt.plot([0, 1], [0, 1], "r--")
    plt.xlim([0, 1])
    plt.ylim([0, 1])
    plt.tight_layout()
    plt.savefig(name+".svg", format='svg')
    plt.savefig(name+".jpeg", format='jpeg')
    plt.savefig(name+".pdf", format='pdf')
    x=pd.concat([x1,x2,x3,x4,x5,x6],axis=1)
    x.columns=['FPR','TPR','FPR','TPR','FPR','TPR','FPR','TPR','FPR','TPR','FPR','TPR']
    return df,x

In [ ]:
def svc_cv(C,gamma):
    val = cross_val_score( 
        SVC(
            kernel='rbf',
            probability=True,
            C=C,
            gamma=gamma,
            random_state=123
        ),
    X_train_val,Y_train_val,scoring='roc_auc', cv=10).mean()
    return val
        
        

In [ ]:
def lgb_cv(n_estimators,subsample, max_depth,colsample_bytree, reg_alpha,reg_lambda,num_leaves,learning_rate):
    val = cross_val_score(
            lgb.LGBMClassifier(boosting_type='gbdt', objective='binary',n_jobs=-1,
                                   colsample_bytree=float(colsample_bytree),
                                   #min_child_samples=int(min_child_samples),
                                   n_estimators=int(n_estimators),
                                   num_leaves=int(num_leaves),
                                   reg_alpha=float(reg_alpha),
                                   reg_lambda=float(reg_lambda),
                                   max_depth=int(max_depth),
                                   subsample=float(subsample),
                                   #min_gain_to_split = float(min_gain_to_split),
                                   learning_rate=float(learning_rate),
                                   random_state=123,is_unbalance=True
        ),
    X_train_val,Y_train_val,scoring='roc_auc', cv=10).mean()
    return val


In [ ]:
def rf_cv(n_estimators, min_samples_split, max_features, max_depth):
    val = cross_val_score(
            RandomForestClassifier(n_estimators=int(n_estimators),
                       min_samples_split=int(min_samples_split),
                       max_features=min(max_features, 0.999),
                       max_depth=int(max_depth),
                       
                       n_jobs=-1,
                       class_weight='balanced',
                       random_state=123
        ),
    X_train_val,Y_train_val,scoring='roc_auc', cv=10).mean()
    return val


In [ ]:
def xgb_cv(n_estimators,subsample, max_depth,colsample_bytree, reg_alpha,reg_lambda,learning_rate):
    val = cross_val_score(
            xgb.XGBClassifier(colsample_bytree=float(colsample_bytree),
                                   #min_child_samples=int(min_child_samples),
                                   n_estimators=int(n_estimators),
                                   
                                   reg_alpha=float(reg_alpha),
                                   reg_lambda=float(reg_lambda),
                                   max_depth=int(max_depth),
                                   subsample=float(subsample),
                                   #min_gain_to_split = float(min_gain_to_split),
                                   learning_rate=float(learning_rate),
        random_state=123
        ),
    X_train_val,Y_train_val,scoring='roc_auc', cv=10).mean()
    return val


In [8]:
X_train_val,Y_train_val,X_test,Y_test,X_all,Y_all=get_data("cv0.8")

In [ ]:
svc_bo = BayesianOptimization(svc_cv,
        { 'C': (0.1,2),'gamma': (0.001,0.1)}
    )

svc_bo.maximize(n_iter=25)

In [ ]:
lgb_bo = BayesianOptimization(
        lgb_cv,
        {
        'colsample_bytree': (0.8,1),
        
        'num_leaves': (16,256),
        'subsample': (0.4, 1),
        'max_depth':(3,5),
        'n_estimators': (100, 1000),
        'reg_alpha':(0,0.015),
        'reg_lambda':(0,0.015),
        
        'learning_rate':(0.0001,0.1)
         },
    )

# 训练
lgb_bo.maximize(n_iter=25)

In [ ]:
xgb_bo = BayesianOptimization(
        xgb_cv,
        {
        'colsample_bytree': (0.8,1),
        
        
        'subsample': (0.4, 1),
        'max_depth':(3,5),
        'n_estimators': (100, 1000),
        'reg_alpha':(0,0.015),
        'reg_lambda':(0,0.015),
        
        'learning_rate':(0.0001,0.1)
         },
    )

# 训练
xgb_bo.maximize(n_iter=25)


In [ ]:
rf_bo = BayesianOptimization(
        rf_cv,
        {'n_estimators': (100, 500),  
               'min_samples_split': (2, 8),
               'max_features': (0.2, 1),
               
               'max_depth': (4, 12)},
         
    )
rf_bo.maximize(n_iter=25)

In [25]:
model1=SVC(probability=True,kernel='rbf',C=svc_bo.max['params']['C'], gamma=svc_bo.max['params']['gamma'])
model2=RandomForestClassifier(random_state=123,class_weight='balanced',max_depth=int(rf_bo.max['params']['max_depth']), max_features=rf_bo.max['params']['max_features'], min_samples_split= int(rf_bo.max['params']['min_samples_split']), n_estimators= int(rf_bo.max['params']['n_estimators']))

model3=xgb.XGBClassifier(random_state=123,colsample_bytree= xgb_bo.max['params']['colsample_bytree'], learning_rate= xgb_bo.max['params']['learning_rate'], 
                      max_depth= int(xgb_bo.max['params']['max_depth']), n_estimators=int(xgb_bo.max['params']['n_estimators']), reg_alpha=xgb_bo.max['params']['reg_alpha'], reg_lambda=xgb_bo.max['params']['reg_lambda'], subsample= xgb_bo.max['params']['subsample'])
model4=LGBMClassifier(random_state=123,class_weight='balanced',colsample_bytree= lgb_bo.max['params']['colsample_bytree'], learning_rate= lgb_bo.max['params']['learning_rate'], 
                      max_depth= int(lgb_bo.max['params']['max_depth']), n_estimators=int(lgb_bo.max['params']['n_estimators']), num_leaves= int(lgb_bo.max['params']['num_leaves']), reg_alpha=lgb_bo.max['params']['reg_alpha'], reg_lambda=lgb_bo.max['params']['reg_lambda'], subsample= lgb_bo.max['params']['subsample'])

    #,scale_pos_weight=5
model5=VotingClassifier(estimators=[('SVC',model1),('RF',model2),('XGB',model3),('LGB',model4)],voting='soft')
model6=get_stacking()

In [9]:
report_cv80_after_tune,x=model_score("cv80_AUC_plot_20240105",X_train_val,Y_train_val,X_test,Y_test,model1, model2, model3, model4, model5, model6)

SVM ROC_AUC: 0.8251998897160187               precision    recall  f1-score   support

           0       0.82      0.60      0.70        93
           1       0.80      0.92      0.85       156

    accuracy                           0.80       249
   macro avg       0.81      0.76      0.78       249
weighted avg       0.81      0.80      0.80       249

RF ROC_AUC: 0.8408464295561071               precision    recall  f1-score   support

           0       0.79      0.68      0.73        93
           1       0.82      0.89      0.86       156

    accuracy                           0.81       249
   macro avg       0.80      0.78      0.79       249
weighted avg       0.81      0.81      0.81       249

XGB ROC_AUC: 0.8261648745519713               precision    recall  f1-score   support

           0       0.80      0.65      0.71        93
           1       0.81      0.90      0.85       156

    accuracy                           0.81       249
   macro avg       0.81      0.77

In [10]:
report_cv80_after_tune

precision    recall  f1-score     support
0              0.823529  0.602151  0.695652   93.000000
1              0.795580  0.923077  0.854599  156.000000
accuracy       0.803213  0.803213  0.803213    0.803213
macro avg      0.809555  0.762614  0.775126  249.000000
weighted avg   0.806019  0.803213  0.795234  249.000000
0              0.787500  0.677419  0.728324   93.000000
1              0.822485  0.891026  0.855385  156.000000
accuracy       0.811245  0.811245  0.811245    0.811245
macro avg      0.804993  0.784222  0.791854  249.000000
weighted avg   0.809418  0.811245  0.807928  249.000000
0              0.800000  0.645161  0.714286   93.000000
1              0.810345  0.903846  0.854545  156.000000
accuracy       0.807229  0.807229  0.807229    0.807229
macro avg      0.805172  0.774504  0.784416  249.000000
weighted avg   0.806481  0.807229  0.802159  249.000000
0              0.703297  0.688172  0.695652   93.000000
1              0.816456  0.826923  0.821656  156.000000
accuracy       0.775100  0.775100  0.775100    0.775100
macro avg      0.759876  0.757548  0.758654  249.000000
weighted avg   0.774191  0.775100  0.774594  249.000000
0              0.787500  0.677419  0.728324   93.000000
1              0.822485  0.891026  0.855385  156.000000
accuracy       0.811245  0.811245  0.811245    0.811245
macro avg      0.804993  0.784222  0.791854  249.000000
weighted avg   0.809418  0.811245  0.807928  249.000000
0              0.777778  0.677419  0.724138   93.000000
1              0.821429  0.884615  0.851852  156.000000
accuracy       0.807229  0.807229  0.807229    0.807229
macro avg      0.799603  0.781017  0.787995  249.000000
weighted avg   0.805125  0.807229  0.804151  249.000000

In [27]:
import pickle
pickle.dump(model1,open("CV0.5_SVC分类_model_20230630.dat","wb"))
pickle.dump(model2,open("CV0.5_RF分类_model_20230630.dat","wb"))
pickle.dump(model3,open("CV0.5_XGB分类_model_20230630.dat","wb"))
pickle.dump(model4,open("CV0.5_LGB分类_model_20230630.dat","wb"))
pickle.dump(model5,open("CV0.5_Voting分类_model_20230630.dat","wb"))
pickle.dump(model6,open("CV0.5_Stacking分类_model_20230630.dat","wb"))